In [1]:

# K partes del grafo 
sizes = [3,2]            


# Grafo k-pártito y politopo P_G 
G = graphs.CompleteMultipartiteGraph(sizes)
n = sum(sizes)
print(f"Grafo  K{tuple(sizes)}   |V|={n}   |E|={G.num_edges()}")


verts = []
for u, v in G.edges(labels=False):
    vec = vector(QQ, [1 if i == u else -1 if i == v else 0 for i in range(n)])
    verts.append(vec); verts.append(-vec)

try:
    P = Polyhedron(vertices=verts, backend='normaliz')
    backend = 'normaliz'          # se creó con Normaliz
except (RuntimeError, ValueError):
    P = Polyhedron(vertices=verts)   # backend por defecto (PPL, cdd…)
    backend = 'other'               # usaremos LattE como motor

# Dimensión, f vector, vértices
print("\n=== Datos de  P_G ===")
print("Dimensión              :", P.dim())
print("f-vector               :", P.f_vector())
print("# vértices (=2|E|)     :", len(P.vertices_list()))


# Polinomio y serie de Ehrhart 
s, t = var('s t')

if backend == 'normaliz':
    Ehr   = P.ehrhart_polynomial(variable=s)      # Normaliz interno
    Serie = P.ehrhart_series(t)                   #   »      »
    engine_used = 'normaliz (backend)'
else:
    Ehr   = P.ehrhart_polynomial(variable=s, engine='latte')
    Serie = P.ehrhart_series(t,          engine='latte')
    engine_used = 'latte'

print(f"\n[Ehrhart con {engine_used}]")
print("H_G(s)                 :", Ehr)
print("F_{P_G}(t)             :", Serie)

# δ-vector
delta_vec  = Serie.numerator().coefficients(sparse=False)
print("δ-vector               :", delta_vec)




Grafo  K(3, 2)   |V|=5   |E|=6



=== Datos de  P_G ===
Dimensión              : 4
f-vector               : (1, 12, 30, 28, 10, 1)
# vértices (=2|E|)     : 12



[Ehrhart con normaliz (backend)]
H_G(s)                 : 4/3*s^4 + 8/3*s^3 + 14/3*s^2 + 10/3*s + 1
F_{P_G}(t)             : (t^4 + 8*t^3 + 14*t^2 + 8*t + 1)/(-t^5 + 5*t^4 - 10*t^3 + 10*t^2 - 5*t + 1)
δ-vector               : [1, 8, 14, 8, 1]


In [2]:
# Anillo de polinomios con coeficientes racionales
R.<s> = PolynomialRing(QQ)

# Campo complejo con 30 cifras decimales (~100 bits)
K = ComplexField(100)

# Todas las raíces numéricas 
Ehr_roots = Ehr.roots(ring=K)      

for z, mult in Ehr_roots:
    print(f"{z}    mult={mult}")


-0.50000000000000000000000000000 - 1.3789081981285038843692812930*I    mult=1
-0.50000000000000000000000000000 - 0.31402576507987792293701473916*I    mult=1
-0.50000000000000000000000000000 + 0.31402576507987792293701473916*I    mult=1
-0.50000000000000000000000000000 + 1.3789081981285038843692812930*I    mult=1


In [3]:
# ───────── AJUSTA AQUÍ ──────────────────────────────────────────────────────
h_spacing  = 1800.0              # AUMENTADO: separación horizontal entre nodos
v_spacing  = 50.0               # separación vertical entre niveles
figsize    = (120, 90)           # AUMENTADO: tamaño de la figura (más ancho)
# ─────────────────────────────────────────────────────────────────────────────

# 1) Calcula la retícula de caras de tu politopo P
faces   = P.face_lattice()
min_dim = min(f.dimension() for f in faces)
max_dim = max(f.dimension() for f in faces)
n_levels = max_dim - min_dim + 1
levels  = [[] for _ in range(n_levels)]
for f in faces:
    idx = (max_dim - f.dimension())
    levels[idx].append(f)

# 2) Crea identificador numérico para vértices 
verts_list = P.vertices_list()
v_id = {tuple(v): i+1 for i, v in enumerate(verts_list)}

def label(face):
    idx = sorted(v_id[tuple(v)] for v in face.vertices())
    return r"$\varnothing$" if not idx else r"$\{" + ",".join(map(str, idx)) + r"\}$"

# 3) Calcula posiciones (x,y)
pos = {}
for d, lvl in enumerate(levels):
    y_pos = d * v_spacing
    if len(lvl) == 1:
        pos[lvl[0]] = (0.0, y_pos)
    else:
        step = h_spacing / (len(lvl) - 1)
        offset = -h_spacing / 2
        for i, f in enumerate(sorted(lvl, key=str)):
            pos[f] = (offset + i * step, y_pos)

# 4) Construye y dibuja el diagrama con líneas color vino
import networkx as nx, matplotlib.pyplot as plt

DG = nx.DiGraph()
DG.add_nodes_from(faces)
DG.add_edges_from(faces.cover_relations())

plt.figure(figsize=figsize, facecolor='white')
nx.draw_networkx_nodes(
    DG, pos,
    node_color="#a2ddfd",      # Color de nodo azul claro
    edgecolors="#EFEEEA",       # Borde blanco perlado
    node_size=10,
    linewidths=1.3,
)

# LÍNEAS EN COLOR VINO (#C5172E) - COINCIDE CON LAS ETIQUETAS
nx.draw_networkx_edges(
    DG, pos, 
    arrows=False, 
    width=1.5,                # Ligeramente más gruesas
    alpha=0.7,                # Menos transparencia
    edge_color='#686D76'       # Color vino
)

# ETIQUETAS
nx.draw_networkx_labels(
    DG, pos, 
    labels={f: label(f) for f in faces}, 
    font_size=15,
    font_color='#C5172E',      # Color vino
    font_weight='bold',
    alpha=0.0
)

plt.axis("off")
plt.show()